In [1]:
import pandas as pd
import re
import nltk
from nltk.corpus import stopwords
from string import punctuation
from nltk.stem import SnowballStemmer
from nltk import sent_tokenize
import gensim
from gensim.models import Word2Vec
import warnings
warnings.filterwarnings('ignore')

In [2]:
translator = str.maketrans('','',punctuation) 
nltk.download('stopwords')
nltk.download('punkt')
stoplist = set(stopwords.words('english'))
stemmer = SnowballStemmer('english')

[nltk_data] Downloading package stopwords to
[nltk_data]     /Users/gigimancinelli./nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package punkt to
[nltk_data]     /Users/gigimancinelli./nltk_data...
[nltk_data]   Package punkt is already up-to-date!


In [3]:
df = pd.read_csv("./data/preprocessed_data_mpv.csv")

In [4]:
for i, row in df.iterrows():
    print(row.TextColumn)
    if i == 50:
        break

  a godfrey man who had been charged with murder in the shooting death of a woman inside a truck in missouri died thursday during a standoff with police in west alton  missouri  amy lynn delacruz  XXXXXX  of cadet  missouri  was identified as the victim found in the truck  according to cpl  barry bayles of the st  charles county  missouri  police department  her body was found early thursday in a tractor trailer in floristell  missouri  according to court records  clyde e  young  XXXXXX  of godfrey  died during a standoff with police at a gas station on u s  XXXXXX in west alton  missouri  near the clark bridge over the mississippi river  police said  bayles said investigators were trying to determine whether young was shot by police or if he died from a self inflicted gunshot  young had called XXXXXXXXX to say his girlfriend was shot in the truck in floristell  according to a probable cause statement filed in st  charles county court by the st  charles police department  young was not

In [5]:
df['TextColumn'] = df['TextColumn'].astype(str)

In [6]:
def remove_unwanted_content(text):
    patterns = [
        r'example video title will go here for this video',
        r'example video title',
        r'will go here for this video',
        r'this video',
        r'click here', 
        r'org',
        r'newsletter',
        r'latest local breaking news',
        r'breaking news', 
        r'news app',
        r'get today',
        r'apple',
        r'google',
        r'play store',
        r'app',
        r'streaming device',
        r'stream live',
        r'live video',
        r'news and updates',
        r'download',
        r'channel',
        r'searching',
        r'youtube',
        r'on demand videos',
        r'here watch',
        r'newscasts',
        r'content', 
        r'anytime',
        r'anywhere',
        r'once a day',
        r'free',
        r'you can now watch',
        r'your phone',
        r'up to speed',
        r'catch up on the latest news and stories',
        r'catch up',
        r'latest news',
        r'latest stories',
        r'review journal',
        r'digital content',
        r'news live',
        r'news',
        r'live',
        r'sign up for our newsletter',
        r'all rights reserved',
        r'check back for updates',
        r'email notifications',
        r'what s your reaction',
        r'your reaction',
        r'facebook',
        r'email',
        r'pic',
        r'chat',
        r'contributed to this report',
        r'this report',
        r'com',
        r'news bulletin press time',
        r'editor s note',
        r'this article was updated on',
        r'twitter',
        r'media group',
        r'stream channel',
        r'report a spelling or grammar error',
        r'please include the headline',
        r'copyright',
        r'smart tv apps',
        r'download our free news',
        r'daily',
        r'headline',
        r'there was a problem',
        r'saving your notification',
        r'your notification has been saved',
        r'saving your notification',
        r'description',
        r'email notifications are only sent once a day',
        r'email notifications',
        r'matching items',
        r'XXXXXX',
        r'XXX',
        r'notifications',
        r'watch'
        
    ]
    for pattern in patterns:
        if isinstance(text, str):
            text = re.sub(pattern, '', text)
            
        else: 
            print(f'there is an issue with this {text}')
    text = re.sub(r'\b[a-zA-Z]\b', '', text)
    text = re.sub(r'\s+', ' ', text).strip()
    return text

In [7]:
df['cleaned'] = df['TextColumn'].apply(remove_unwanted_content)

In [8]:
for i, row in df.iterrows():
    print(row.cleaned)
    if i == 50:
        break

godfrey man who had been charged with murder in the shooting death of woman inside truck in missouri died thursday during standoff with police in west alton missouri amy lynn delacruz of cadet missouri was identified as the victim found in the truck according to cpl barry bayles of the st charles county missouri police department her body was found early thursday in tractor trailer in floristell missouri according to court records clyde young of godfrey died during standoff with police at gas station on in west alton missouri near the clark bridge over the mississippi river police said bayles said investigators were trying to determine whether young was shot by police or if he died from self inflicted gunshot young had called to say his girlfriend was shot in the truck in floristell according to probable cause statement filed in st charles county court by the st charles police department young was not at the truck when police arrived but he later called an officer to say that he fired 

In [9]:
stop_words = set(stopwords.words('english'))

In [10]:
stop_words

{'a',
 'about',
 'above',
 'after',
 'again',
 'against',
 'ain',
 'all',
 'am',
 'an',
 'and',
 'any',
 'are',
 'aren',
 "aren't",
 'as',
 'at',
 'be',
 'because',
 'been',
 'before',
 'being',
 'below',
 'between',
 'both',
 'but',
 'by',
 'can',
 'couldn',
 "couldn't",
 'd',
 'did',
 'didn',
 "didn't",
 'do',
 'does',
 'doesn',
 "doesn't",
 'doing',
 'don',
 "don't",
 'down',
 'during',
 'each',
 'few',
 'for',
 'from',
 'further',
 'had',
 'hadn',
 "hadn't",
 'has',
 'hasn',
 "hasn't",
 'have',
 'haven',
 "haven't",
 'having',
 'he',
 'her',
 'here',
 'hers',
 'herself',
 'him',
 'himself',
 'his',
 'how',
 'i',
 'if',
 'in',
 'into',
 'is',
 'isn',
 "isn't",
 'it',
 "it's",
 'its',
 'itself',
 'just',
 'll',
 'm',
 'ma',
 'me',
 'mightn',
 "mightn't",
 'more',
 'most',
 'mustn',
 "mustn't",
 'my',
 'myself',
 'needn',
 "needn't",
 'no',
 'nor',
 'not',
 'now',
 'o',
 'of',
 'off',
 'on',
 'once',
 'only',
 'or',
 'other',
 'our',
 'ours',
 'ourselves',
 'out',
 'over',
 'own',
 'r

In [11]:
def normalize_text(doc):
    doc = doc.replace('\r', ' ').replace('\n', ' ')
    words = doc.split() 
    nostop = [w for w in words if w not in stop_words] 
    stemmed = [stemmer.stem(w) for w in nostop] 
    return stemmed
  
def get_sentences(doc):
    sent=[]
    for raw in sent_tokenize(doc):
        raw2 = normalize_text(raw)
        sent.append(raw2)
    return sent

In [12]:
df['sentences'] = df['cleaned'].apply(get_sentences)

In [13]:
for i, row in df.iterrows():
    print(row.sentences)
    if i == 50:
        break

[['godfrey', 'man', 'charg', 'murder', 'shoot', 'death', 'woman', 'insid', 'truck', 'missouri', 'die', 'thursday', 'standoff', 'polic', 'west', 'alton', 'missouri', 'ami', 'lynn', 'delacruz', 'cadet', 'missouri', 'identifi', 'victim', 'found', 'truck', 'accord', 'cpl', 'barri', 'bayl', 'st', 'charl', 'counti', 'missouri', 'polic', 'depart', 'bodi', 'found', 'earli', 'thursday', 'tractor', 'trailer', 'floristel', 'missouri', 'accord', 'court', 'record', 'clyde', 'young', 'godfrey', 'die', 'standoff', 'polic', 'gas', 'station', 'west', 'alton', 'missouri', 'near', 'clark', 'bridg', 'mississippi', 'river', 'polic', 'said', 'bayl', 'said', 'investig', 'tri', 'determin', 'whether', 'young', 'shot', 'polic', 'die', 'self', 'inflict', 'gunshot', 'young', 'call', 'say', 'girlfriend', 'shot', 'truck', 'floristel', 'accord', 'probabl', 'caus', 'statement', 'file', 'st', 'charl', 'counti', 'court', 'st', 'charl', 'polic', 'depart', 'young', 'truck', 'polic', 'arriv', 'later', 'call', 'offic', 'sa

In [14]:
sentences = []
for i, row in df.iterrows():
    sentence = row.sentences
    for sent in sentence:
        sentences.append(sent)

In [15]:
sentences

[['godfrey',
  'man',
  'charg',
  'murder',
  'shoot',
  'death',
  'woman',
  'insid',
  'truck',
  'missouri',
  'die',
  'thursday',
  'standoff',
  'polic',
  'west',
  'alton',
  'missouri',
  'ami',
  'lynn',
  'delacruz',
  'cadet',
  'missouri',
  'identifi',
  'victim',
  'found',
  'truck',
  'accord',
  'cpl',
  'barri',
  'bayl',
  'st',
  'charl',
  'counti',
  'missouri',
  'polic',
  'depart',
  'bodi',
  'found',
  'earli',
  'thursday',
  'tractor',
  'trailer',
  'floristel',
  'missouri',
  'accord',
  'court',
  'record',
  'clyde',
  'young',
  'godfrey',
  'die',
  'standoff',
  'polic',
  'gas',
  'station',
  'west',
  'alton',
  'missouri',
  'near',
  'clark',
  'bridg',
  'mississippi',
  'river',
  'polic',
  'said',
  'bayl',
  'said',
  'investig',
  'tri',
  'determin',
  'whether',
  'young',
  'shot',
  'polic',
  'die',
  'self',
  'inflict',
  'gunshot',
  'young',
  'call',
  'say',
  'girlfriend',
  'shot',
  'truck',
  'floristel',
  'accord',
  '

In [16]:
df.to_csv("data/mpv_clean_pattern_stop.csv")

## word2vec
We test different embedding dimensions and different witndow sizes to get the best vector representations. While it is hard to properly define a measure that helps us tune the hyperparameters, we evaluate based on classical similarities between words.

In [17]:
num_words_list = [100, 200, 300]
windows_val = [3, 5, 7]
models = {'dim': [], 'window': [], 'model': []}
for num_words in num_words_list:
    for wind in windows_val:
        model = Word2Vec (sentences, 
                          vector_size = num_words, 
                          min_count=1,
                          window=wind,
                          seed=42, 
                          workers=8)
        models['model'].append(model)
        models['dim'].append(num_words)
        models['window'].append(wind)

In [18]:
models

{'dim': [100, 100, 100, 200, 200, 200, 300, 300, 300],
 'window': [3, 5, 7, 3, 5, 7, 3, 5, 7],
 'model': [<gensim.models.word2vec.Word2Vec at 0x323d37d90>,
  <gensim.models.word2vec.Word2Vec at 0x323b16f90>]}

In [19]:
query = 'man'
for i in range (len (models['model'])):
    model = models['model'][i]
    print (f"Model with vector dimension={models['dim'][i]} and window size={models['window'][i]}")
    for item in model.wv.most_similar(query, topn=5):
        print(item)
    print()

Model with vector dimension=100 and window size=3
('woman', 0.8233712315559387)
('suspect', 0.7913069128990173)
('person', 0.7461119294166565)
('gunman', 0.6431960463523865)
('individu', 0.6423617601394653)

Model with vector dimension=100 and window size=5
('woman', 0.8009001016616821)
('suspect', 0.7468323707580566)
('person', 0.7037762403488159)
('gunman', 0.5670594573020935)
('someon', 0.5579000115394592)

Model with vector dimension=100 and window size=7
('woman', 0.7603464722633362)
('suspect', 0.7121824622154236)
('person', 0.6670485734939575)
('someon', 0.5530003309249878)
('author', 0.5403410196304321)

Model with vector dimension=200 and window size=3
('woman', 0.7396266460418701)
('suspect', 0.6932824850082397)
('person', 0.6836258172988892)
('gunman', 0.6073805689811707)
('individu', 0.5926148891448975)

Model with vector dimension=200 and window size=5
('woman', 0.7237046360969543)
('suspect', 0.6709511876106262)
('person', 0.653952956199646)
('gunman', 0.5655854940414429)

#### Now we can extract the best model from the dictionary and save it. It will be the one used in our main analysis. The best model correspond to 100-dimensional vector with window size of 3.

In [20]:
model_ = models['model'][0]

In [21]:
model_.save("./model/word2vec.model")

In [36]:
for item in model_.wv.most_similar(positive= ['black', 'man'],  topn=5):
    print(item)

('teen', 0.6420449614524841)
('woman', 0.610974907875061)
('white', 0.573694109916687)
('suspect', 0.5687180161476135)
('male', 0.5513501763343811)


In [35]:
for item in model_.wv.most_similar(positive= ['man', 'white'],  topn=5):
    print(item)

('male', 0.6791019439697266)
('suspect', 0.6773388385772705)
('woman', 0.6446460485458374)
('driver', 0.6170333027839661)
('teen', 0.6123615503311157)


### We repeat the same analysis to get embeddings for article before and after George Floyd (May 25, 2020). We will use the best hyperparameters obtained before but we will train two new word2vec models: one for articles related to events that occoured before George Floyd, and one for articles related to events occouring after George Floyd. 

In [22]:
df_before_floyd = df[df.after_Floyd == False]
df_after_floyd = df[df.after_Floyd == True]

In [23]:
sentences_before = []
for i, row in df_before_floyd.iterrows():
    sentence_b = row.sentences
    for sent in sentence_b:
        sentences_before.append(sent)

In [24]:
sentences_after = []
for i, row in df_after_floyd.iterrows():
    sentence_a = row.sentences
    for sent in sentence_a:
        sentences_after.append(sent)

In [25]:
model_before = Word2Vec (sentences_before, 
                          vector_size = 100, 
                          min_count=1,
                          window=3,
                          seed=42, 
                          workers=8)

In [26]:
print (f'Model before George Floyd')
for item in model_before.wv.most_similar(query, topn=5):
    print(item)

Model before George Floyd
('woman', 0.8139071464538574)
('suspect', 0.7855895161628723)
('gunman', 0.7297147512435913)
('person', 0.6710433959960938)
('teen', 0.6588177680969238)


In [27]:
model_after = Word2Vec (sentences_after, 
                          vector_size = 100, 
                          min_count=1,
                          window=3,
                          seed=42, 
                          workers=8)

In [28]:
print (f'Model after George Floyd')
for item in model_after.wv.most_similar(query, topn=5):
    print(item)

Model after George Floyd
('woman', 0.7776929140090942)
('suspect', 0.767963171005249)
('person', 0.7253653407096863)
('gunman', 0.6589791178703308)
('individu', 0.6556470394134521)


In [30]:
#get dimension of the embedding matrix
model_before.wv.vectors.shape

(27377, 100)

In [29]:
model_before.save("./model/word2vec_before_floyd.model")
model_after.save("./model/word2vec_after_floyd.model")